In [7]:
import os
import sys

# from embeddings.llama import Embedder
sys.path.append('/root/home/BA_QA_HSMA/backendd')
from embeddings.llama import Embedder
from transformers import LlamaForCausalLM, LlamaTokenizer
import torch
from database.es_handler import ElasticSearchData
from tqdm import tqdm
import pickle
from transformer_llama import LlamaTransformerEmbeddings

In [9]:
model_path = "../models/tmp/llama-13b-hf"
embeddings_model = LlamaTransformerEmbeddings(model_path)

The tokenizer class you load from this checkpoint is not the same type as the class this function is called from. It may result in unexpected tokenization. 
The tokenizer class you load from this checkpoint is 'LLaMATokenizer'. 
The class this function is called from is 'LlamaTokenizer'.
Loading checkpoint shards:   0%|          | 0/41 [00:00<?, ?it/s]/home/maydane/miniconda3/envs/backend/lib/python3.10/site-packages/torch/_utils.py:776: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  return self.fget.__get__(instance, owner)()
Loading checkpoint shards: 100%|██████████| 41/41 [05:15<00:00,  7.70s/it]


In [30]:
list(embeddings_model.tokenizer.vocab.keys())[5000:5020]

AttributeError: 'LlamaTokenizer' object has no attribute 'vocab'

In [32]:
tokenizer= embeddings_model.tokenizer
text= "After stealing money from the bank vault, the bank robber was seen " \
       "fishing on the Mississippi river bank."

In [33]:
# Split the sentence into tokens.
tokenized_text = tokenizer.tokenize(text)

# Map the token strings to their vocabulary indeces.
indexed_tokens = tokenizer.convert_tokens_to_ids(tokenized_text)


In [35]:
segments_ids = [1] * len(tokenized_text)
segments_ids

[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]

In [36]:
tokens_tensor = torch.tensor([indexed_tokens])
segments_tensors = torch.tensor([segments_ids])

In [25]:
tokenized_text = embeddings_model.tokenizer.tokenize("After stealing money from the bank vault, the bank robber was seen " \
       "fishing on the Mississippi river bank.")
for i, token_str in enumerate(tokenized_text):
  print (i, token_str)



0 ▁After
1 ▁ste
2 aling
3 ▁money
4 ▁from
5 ▁the
6 ▁bank
7 ▁v
8 ault
9 ,
10 ▁the
11 ▁bank
12 ▁rob
13 ber
14 ▁was
15 ▁seen
16 ▁fish
17 ing
18 ▁on
19 ▁the
20 ▁Mississippi
21 ▁river
22 ▁bank
23 .


In [24]:
from scipy.spatial.distance import cosine


In [26]:
# Stores the token vectors, with shape [22 x 3,072]
token_vecs_cat = []

# `token_embeddings` is a [22 x 12 x 768] tensor.

# For each token in the sentence...
for token in token_embeddings:
    
    # `token` is a [12 x 768] tensor

    # Concatenate the vectors (that is, append them together) from the last 
    # four layers.
    # Each layer vector is 768 values, so `cat_vec` is length 3,072.
    cat_vec = torch.cat((token[-1], token[-2], token[-3], token[-4]), dim=0)
    
    # Use `cat_vec` to represent `token`.
    token_vecs_cat.append(cat_vec)

print ('Shape is: %d x %d' % (len(token_vecs_cat), len(token_vecs_cat[0])))

NameError: name 'token_embeddings' is not defined

In [ ]:
# Stores the token vectors, with shape [22 x 768]
token_vecs_sum = []

# `token_embeddings` is a [22 x 12 x 768] tensor.

# For each token in the sentence...
for token in token_embeddings:

    # `token` is a [12 x 768] tensor

    # Sum the vectors from the last four layers.
    sum_vec = torch.sum(token[-4:], dim=0)
    
    # Use `sum_vec` to represent `token`.
    token_vecs_sum.append(sum_vec)

print ('Shape is: %d x %d' % (len(token_vecs_sum), len(token_vecs_sum[0])))

In [ ]:
# Calculate the cosine similarity between the word bank 
# in "bank robber" vs "river bank" (different meanings).
diff_bank = 1 - cosine(token_vecs_sum[10], token_vecs_sum[19])

# Calculate the cosine similarity between the word bank
# in "bank robber" vs "bank vault" (same meaning).
same_bank = 1 - cosine(token_vecs_sum[10], token_vecs_sum[6])

print('Vector similarity for  *similar*  meanings:  %.2f' % same_bank)
print('Vector similarity for *different* meanings:  %.2f' % diff_bank)